# Ciencia de Datos y Lenguaje Natural  -  **Notebook 3** 
## Redes Neuronales y Word Embeddings

En este notebook se trabajará con redes neuronales y word embeddings. El objetivo es indicar si una oración expresa un juicio positivo o negativo, al igual que en el notebook anterior, pero en este caso utilizando word embeddings y clasificadores basados redes neuronales. 

Al igual que en el notebook 2 se trabajará con el corpus CDLN-Senti formado por oraciones simples anotadas según su orientación semántica (positiva, 0; negativa, 1). El corpus se generó a partir de comentarios de usuarios en los sitios de Amazon, IMDB y Yelp. Se encontraba disponible en inglés y fue traducido al español por Google translate. 

Se resolverá el problema propuesto por 3 estrategias distintas según el tratamiento de secuencias y el tipo de la red utilizado. En el primero se debe utilizar una red completamente conectada *feed forward* y la entrada debe representarse como un vector mediante una operación de los vectores de las palabras (ej. centroide). En el segundo enfoque se debe utilizar una red recurrente para la entrada. Finalmente, en el tercer enfoque se debe utilizar una red de tipo transformer. Se deben reportar los resultados obtenidos. 


#### Indique nombre, número de cédula y que carrera está cursando

In [ ]:
__author__ = "Nombre Apellido"
__cedula__ = "1.234.567-8"
__origen__ = "Grado. Ing. Computación"

## Lectura de datos (corpus y léxicos)

Se dispone de dos léxicos para el español, uno de palabras positivas (palabras-pos.txt) y otro de palabras negativas (palabras-neg.txt). Descarguelos del eva del curso. (Los léxicos fueron extraídos de: https://www.kaggle.com/datasets/rtatman/sentiment-lexicons-for-81-languages?resource=download)

Se dispone además de un corpus con los datos de las opiniones en el formato "frase|valor", donde "frase" es la frase a analizar (Ej. "Me encantó. Volveré.") y "valor" es 0 o 1. Este coprpus se encuentra fraccionado en entrenamiento (senti-train.csv), validación (senti-val.csv) y test (senti-test.csv). 

En el siguiente bloque de código se leen y cargan en memoria los léxicos y el corpus de análisis de sentimiento. Estos recursos serán utilizados a lo largo de todo el notebook.  

In [ ]:
import numpy as np
import os
import csv
import sklearn

def read_data(path):
    import csv
    rows=[]
    with open(path, encoding='utf-8') as doc:
        csvreader = csv.reader(doc, delimiter ='|', quoting=csv.QUOTE_NONE)
        for i,row in enumerate(csvreader):
            rows.append(row)
    if len(rows)>0 and len(rows[0])==1:
        rows = [r[0] for r in rows]
    return rows


dtrain = read_data('./senti-train.csv')
dval = read_data('./senti-val.csv')
dtest = read_data('./senti-test.csv')
lexpos = read_data('./palabras-pos.txt')
lexneg = read_data('./palabras-neg.txt')

**Cantidad de elementos de corpus y léxicos**

En el siguiente bloque de código se despliega la cantidad de entradas positivas y negativas en cada partición (train, val, test) del corpus; y la cantidad de elementos de los léxicos (positivo y negativo).

In [ ]:
lenx = lambda x: (len(x), len([d for d in x if d[1]=='0']), len([d for d in x if d[1]=='1']))
print('Train (tot,neg,pos):', lenx(dtrain))
print('Val   (tot,neg,pos):', lenx(dval))
print('Test  (tot,neg,pos):', lenx(dtest))
print('Lex Pos:', len(lexpos))
print('Lex Neg:', len(lexneg))

# Word Embeddings

Un *word embedding* es una representación vectorial del significado de las palabras obtenida a partir del uso del lenguaje. Los métodos para obtener *word embeddings* principalmente usan dos tipos de información:
- el contexto de uso de las palabras (coocurrencia de palabras)
- composición de la palabra (*subword*)

Una palabra puede tener varios significados (homonímia y polisemia). Al usar el lenguaje, inferimos el significados adecuado de cada palabra a partir del contexto. En cuanto refiere a los *word embeddings*, existen dos tipos:
- Estáticos: se tiene un único vector que representa todos los significados de la palabra.
- Dinámicos o contextualizados: se tiene un vector por cada ocurrencia de la palabra, distintos usos de las palabras son representados por vectores distintos. 

En esta parte experimentaremos con *word embeddings* estáticos. 

##### Instalar librería y cargar modelo preentrenado

Escoja un modelo de *word embeddings* preentrenado que esté disponible públicamente (Ej. https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.es.300.bin.gz) y una librería para su manipulación (Ej. https://fasttext.cc/docs/en/python-module.html). Además, puede implementar rutinas auxiliares que considere necesarias.

A continuación escriba los comandos necesarios para instalar la librería y descargar el modelo. En caso de implementar alguna funcionalidad también escribila a continuación. 

In [ ]:
# ESCRIBA AQUI SU CODIGO

#Ejemplo: 
#!wget https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.es.300.bin.gz
#pip install fasttext

##### Cargar modelo

A continuación escriba el código para cargar el modelo en memoria. Utilice el nombre de variable 'wemb' para este modelo, será utilizado en las siguientes secciones. 


In [ ]:
# ESCRIBA AQUI SU CODIGO

#Ejemplo:
#import fasttext
#wemb = fasttext.load_model("./cc.es.300.bin")

##### Caclcular la similitud coseno entre 

Con un modelo de *word embeddings* es posible obtener la similitud semántica entre palabras utilizando funciones distancia o similitud entre vectores. Un tipo de similitud entre vectores habitual es la similitud coseno: 

<center> $simcos(\vec{x},\vec{y}) = \frac{\vec{x}.\vec{y}} {||x||.||y||} = cos(\theta) $ </center>

donde $\theta$ es el ángulo entre los vectores. 

Codifique a continuación una función que devuelva la similitud coseno entre las representaciones vectoriales de dos palabras.

In [ ]:
# ESCRIBA AQUI SU CODIGO

from sklearn.metrics.pairwise import cosine_similarity

def cosine_we(w1,w2, wemb=wemb):
    # ...
     

A continuación se despliega la similitud coseno entre los vectores de los siguientes pares de palabras:
- ('perro','canino'), ('perro','chihuahua'),('perro','gato'), ('perro','tortuga'), ('perro','ballena'), ('tortuga','ballena'), ('perro','blanco'), ('pregunta','ballena'),('pregunta','respuesta'),('pregunta','interrogante')

In [ ]:
pares = [('perro','canino'), ('perro','chihuahua'),('perro','gato'), ('perro','tortuga'), 
     ('perro','ballena'), ('tortuga','ballena'), ('perro','blanco'), 
     ('pregunta','ballena'),('pregunta','respuesta'),('pregunta','interrogante')]

for w1,w2 in pares:
    print(w1,w2,cosine_we(w1,w2))

Despliegue a continuación la similitud coseno de pares palabras que considere interesantes:

In [ ]:
# ESCRIBA AQUI SU CODIGO

##### Palabras más similares: 

A continuación despliegue las 5 palabras más similares a las siguientes palabras:
- 'perro', 'ballena', 'pregunta', 'selva', 'Ibarborou', 'Turing'

Mida el tiempo de ejecución de la celda usando %%timeit.

In [ ]:
%%timeit -r 1 -n 1

palabras = ['perro', 'ballena', 'pregunta', 'selva', 'Ibarbourou', 'Turing'] 

# ESCRIBA AQUI SU CODIGO

Despliegue a continuación las 10 palabras más similares a palabras que considere interesantes. 

In [ ]:
# ESCRIBA AQUI SU CODIGO

##### Analogías de palabras:

Los *word embeddings* representan analogías entre pares de palabras mediante la diferencia de vectores. Por ejemplo, si consideramos que 'ver' es a 'viendo' como 'ir' a 'yendo' (notación ver:viendo::ir:yendo) se tiene que

$(\vec{x}_{ver} - \vec{x}_{viendo}) \sim  (\vec{x}_{ir} - \vec{x}_{yendo})$

y por lo tanto

$ \vec{x}_{ir} + (\vec{x}_{viendo} - \vec{x}_{ver}) \sim   \vec{x}_{yendo}$

es decir que con las representaciones de 'ir', 'ver' y 'viendo' se puede intentar recuperar/responder 'yendo'. 



A continuación despliegue las 5 palabras más próximas como respuesta las siguientes preguntas de analogías de palabras:
- hombre:mujer::rey:?
- saltar:saltando::correr:?
- ver:viendo::ir:?
- francia:parís::uruguay:?
- francia:parís::alemania:?

Mida el tiempo de ejecución de la celda usando %%timeit.

In [ ]:
%%timeit -r 1 -n 1

# ESCRIBA AQUI SU CODIGO

##### Correlación de rangos de Spearman en conjuntos de palabras similares o relacionadas 


Calcule la correlación de rangos de Spearman del *word embedding* utilizado, en los siguientes conjuntos:

- es-ws353:  https://github.com/Lambda-3/Gold-Standards/blob/master/SemR-11/Multilingual_Wordpairs/es-ws353.dataset
- es-simlex: https://github.com/Lambda-3/Gold-Standards/blob/master/SemR-11/Multilingual_Wordpairs/es-simlex.dataset


Sugerencia: Considere la función 'spearmanr' de 'scipy.stats'




In [ ]:
# ESCRIBA AQUI SU CODIGO

##### Distancia entre textos usando centroide:

En esta sección calcularemos la distancia entre dos textos a partir de una operación (ej. centroide) entre los vectores de sus palabras. 

Defina una función para vectorizar un texto con los siguientes tres modos: 

- mean : retorna el promedio de los vectores de palabras (centroide)
- max : retorna el máximo de los vectores de palabras componente a componente
- list: retorna la lista de vectores de palabras (puede resultar útil para modelos de RNN)


In [ ]:
from nltk.tokenize import word_tokenize

def vectorize_sentence(sent, wemb=wemb, mod='mean'):
    l = [wemb[w] for w in word_tokenize(sent)]
    if mod == 'mean':
        # ESCRIBA AQUI SU CODIGO
    elif mod == 'max':
        return np.max(l, axis=0)
    elif mod == 'list':
        # ESCRIBA AQUI SU CODIGO

Codifique la siguiente función que recibe dos oraciones y devuelve la distancia coseno de las representaciones de máximo o centroide definidas anteriormente:

In [ ]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

def sentence_sim(sent1, sent2, mod='mean'):
    # ESCRIBA AQUI SU CODIGO

Obtenga la similitud coseno entre los siguientes pares de oraciones usando el máximo y el centroide de los vectores de las palabras de cada oración:

- 'me gustó mucho', 'es muy buena'
- 'no me gustó mucho', 'es muy buena'
- 'me gustó mucho', 'es muy mala'
- 'me gustó mucho', 'me encantó'
- 'me gustó mucho', 'mañana quizá llueva'
- 'estuvo soleado hoy', 'mañana quizá llueva'


In [ ]:
# ESCRIBA AQUI SU CODIGO

###### Pregunta

¿Qué observa respecto a la similitud de oraciones usando centroide o máximo ? ¿Cómo se podrían mejorar los resultados?

**Respuesta:**

***Escriba aquí su respuesta***

# Neural Netowrks: Multi-layer Feedforward Network

En esta parte experimentará con los *word embeddings* preentrenados cargados en la parte anterior y modelos de redes neuronales completamente conectadas de tipo *feedforward*. Este tipo de modelo recibe un vector como entrada, por lo tanto para ser utilizados con secuencias de vectores como entrada (por ejemplo para clasificar texto) **es necesario tranformar una secuencia de vectores de largo variable a un vector de una dimensión predeterminada**. 

Para esto existen varias alternativas, por ejemplo considerar un tamaño máximo de oración y **concatenar** los vectores de la entrada, truncando en caso de que supere el tamaño máximo o rellenando en caso de que el largo sea menor (*padding*). Otra alternativa es considerar una **operación numérica** de los vectores como el promedio (**centroide**) o **máximo** elemento a elemento. 


##### Preparar datos y definición del modelo

Defina un modelo de red neuronal para clasificar sentimiento que use como entrada una representación vectorial del texto (ej. centroide). Utilice la función para vectorizar usando centroido o máximo definida anteriormente para preparar los datos para ser utilizados por el modelo definido.


In [ ]:
import torch.utils.data

batch_size = 64

dtrain_vec = # ESCRIBA AQUI SU CODIGO
dval_vec = # ESCRIBA AQUI SU CODIGO
dtest_vec = # ESCRIBA AQUI SU CODIGO

train_loader = torch.utils.data.DataLoader(dtrain_mean, batch_size=batch_size, shuffle=True)
val_loader = torch.utils.data.DataLoader(dval_mean, batch_size=1, shuffle=True)
test_loader = torch.utils.data.DataLoader(dtest_mean, batch_size=1, shuffle=False)

In [ ]:
# ESCRIBA AQUI SU CODIGO

import torch
import torch.nn as nn
import torch.nn.functional as F


class Net(nn.Module):

    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(300, 50)
        self.fc2 = nn.Linear(50, 1)
        self.drop = nn.Dropout(0.2)
        

    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = self.drop(x)
        x = F.self.fc2(x)
        return x


##### Entrenar modelo

Instancie el modelo definido anteriormente.

In [ ]:
net = Net()
print(net)

Función de pérdida y optimizador:

In [ ]:
import torch.optim as optim

criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(net.parameters(), lr=0.001)


Ciclo de entrenamiento:

In [ ]:
best_val = None

for epoch in range(1,20):  
    # train
    running_loss = 0.0
    for i, (inputs, labels) in enumerate(train_loader):
        # forward pass
        outputs = net(inputs)
        # backward pass
        optimizer.zero_grad()
        loss = criterion(outputs, labels.unsqueeze(1))
        loss.backward()
        optimizer.step()
        
        # print (every 10 mini-batches)
        running_loss += loss.item()
        if i % 10 == 9:    
            print(f'{epoch} [{i+1:3d}] loss: {running_loss / 10:.3f} ')
            running_loss = 0.0
            
    # validation loss
    running_loss_val = 0.0
    i_val = 0
    net.eval() 
    for x_val, y_val in val_loader:
        i_val += 1
        output_val = net(x_val)
        loss_val = criterion(output_val, y_val.unsqueeze(1))
        running_loss_val += loss_val.item()
    loss_val = running_loss_val / i_val
    best_val = loss_val if (best_val is None) else best_val 
    print(f'{epoch} [   ] val_loss: {loss_val :.3f}')

    # checkpoint (save)
    if loss_val <= best_val:
        best_val = loss_val
        torch.save({
        'epoch': epoch,
        'model_state_dict': net.state_dict(),
        'loss': loss.item(),
        }, './chckpoint.tmp.pt')
        print(f'Checkpoint ({loss_val:.3f})')

# load checkpoint
print('Cargando checkpoint...')
checkpoint = torch.load('./chckpoint.tmp.pt')
print(f'Checkpoint epoch {checkpoint["epoch"]}')
net.load_state_dict(checkpoint['model_state_dict'])
                
print('Fin entrenamiento')

##### Evaluar modelo

Utilice la siguiente función para reportar los resultados obtenidos. Utilice los conjuntos train y val para ajustar los hiperparámetros de su modelo.

In [ ]:
from sklearn.metrics import classification_report

def evaluate_model(model, corpus):
    x,y = zip(*corpus)
    x = torch.tensor(np.array(x))
    y = np.array(y)
    model.eval()
    with torch.no_grad():
        y_pred = model(x)
        y_pred = torch.sigmoid(y_pred)
        y_pred = torch.round(y_pred)
        y_pred = y_pred.detach().numpy()
    print(classification_report(y, y_pred))


In [ ]:
# Resultados en train y val
print("Resultados train:")
evaluate_model(net, dtrain_mean)

print("Resultados val:")
evaluate_model(net, dval_mean)

##### Resultados

Reporte los resultados obtenidos con su modelo en test (luego de elegir hiperparámetros).


In [ ]:
print("Resultados test:")
evaluate_model(net, dtest_mean)

# Neural Netowrks: RNN (Opcional)

Extienda los experimentos realizados en la parte anterior utilizando un modelo de red neuronal recurrente (ej. LSTM).  

##### Preparar datos y definición del modelo

In [ ]:
# ESCRIBA AQUI SU CODIGO

##### Entrenar modelo

In [ ]:
# ESCRIBA AQUI SU CODIGO

##### Evaluar modelo

In [ ]:
# ESCRIBA AQUI SU CODIGO

# Neural Networks: Transformer (Robertuito)

En esta sección abordará la tarea con un transformer preentrenado. 

Utilizaremos Robertuito:
- https://huggingface.co/pysentimiento/robertuito-sentiment-analysis?text=Te+quiero.+Te+amo.
 

###### Instalación

Instale Robertuito:

In [ ]:
!pip install pysentimiento

###### Instanciación

Instancie Robertuito para realizar análisis de sentmiento en español:

In [ ]:
# ESCRIBA AQUI SU CODIGO

###### Preparación de datos

Prepare el conjunto de datos para ser etiquetado por Robertuito:

In [ ]:
# ESCRIBA AQUI SU CODIGO

###### Ejecución de Robertuito

Detecte el sentimiento utilizando Robertuito en el dataset impartido. Realice una interpretación de la salida de Robertuito que considere conveniente para etiquetar los datos en el formato adecuado.

In [ ]:
# ESCRIBA AQUI SU CODIGO

###### Resultados obtenidos

Reporte los resultados obtenidos.

In [ ]:
# ESCRIBA AQUI SU CODIGO